In [1]:
import pandas as pd
import numpy as np
import re
import json
import numpy as np
import timeit 
from datetime import datetime

In [2]:
# Cufflinks wrapper on plotly
import cufflinks
from IPython.core.interactiveshell import InteractiveShell
InteractiveShell.ast_node_interactivity = 'all'

from plotly.offline import iplot
cufflinks.go_offline()

# Set global theme

import plotly.figure_factory as ff

import plotly.graph_objects as go

In [3]:
from sklearn.model_selection import train_test_split

In [4]:
#Selecting a central city point to center all graphs around - Swietokrzyska Subway 
center_coors=52.235176, 21.008393

In [5]:
df=pd.read_excel("RE_models_input.xlsx")

In [6]:
df.columns

Index(['Id', 'Area', 'Price', 'latitude', 'longitude', 'build_year',
       'building_floors_num', 'rooms_num', 'City', 'subdistrict', 'market',
       'Building_material', 'Building_ownership', 'Building_type',
       'Construction_status', 'floor_no', 'Heating', 'Windows_type',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm

In [7]:
df['rooms_num']=np.where(df['rooms_num']=="more",10,df['rooms_num'])

In [8]:
df.drop(columns=['floor_no',"City","district_old",'price_decrease_from_20k','price_decrease_per_10min'],inplace=True)

In [9]:
df.columns

Index(['Id', 'Area', 'Price', 'latitude', 'longitude', 'build_year',
       'building_floors_num', 'rooms_num', 'subdistrict', 'market',
       'Building_material', 'Building_ownership', 'Building_type',
       'Construction_status', 'Heating', 'Windows_type',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm',
       'Security_

In [10]:
df["distance_driving"]=(df.distance_driving_8AM+df.distance_return_driving_5PM)/2
df["distance_transit"]=(df.distance_transit_8AM+df.distance_return_transit_5PM)/2
df["time_driving"]=(df.time_driving_8AM+df.time_return_driving_5PM)/2
df["time_transit"]=(df.time_return_transit_5PM+df.time_transit_8AM)/2

In [11]:
df.drop(columns=['distance_transit_8AM', 'time_transit_8AM', 'distance_driving_8AM',
       'time_driving_8AM', 'distance_return_transit_5PM',
       'time_return_transit_5PM', 'distance_return_driving_5PM',
       'time_return_driving_5PM'],inplace=True)

# Data exploration

## Category composition

In [12]:
unique_features=["district","market","Building_material","Building_ownership","Building_type","Construction_status","Heating",
"Windows_type"]

In [13]:
import plotly.express as px

In [14]:
for feature in unique_features:
    feature_list=["Id"]
    feature_list.append(feature)

    df_temp=df[feature_list].groupby(feature, as_index=False).count()
    df_temp.rename(columns={"Id":"share"},inplace=True)
    df_temp.sort_values(by="share",inplace=True, ascending=False)
    df_temp["share"]=df_temp["share"]/df.shape[0]
    df_temp["share"]=np.around(df_temp["share"],3)*100
    df_temp["colour"]=np.where(df_temp[feature]=="not_specified","missing_data","valid_data")
    
    fig = px.bar(df_temp, x=feature, y='share', color="colour",
                 color_discrete_sequence=["blue", "red"],
                 category_orders={"colour": ["valid_data", "missing_data"]},)
    print("\n Feature summary for {} - Share of category within whole sample".format(feature))
    fig.show()
    print("----------------------------------------------------------------------------------------------------------------------------\n\n\n")

    


 Feature summary for district - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for market - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Building_material - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Building_ownership - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Building_type - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Construction_status - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Heating - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------




 Feature summary for Windows_type - Share of category within whole sample


----------------------------------------------------------------------------------------------------------------------------





## Average unit price by feature 

In [15]:
for feature in unique_features:
    feature_list=["unit_price"]
    feature_list.append(feature)

    df_temp=df[feature_list]
    
    print("\n Unit price distribution in split by {}".format(feature))
    
    fig = fig = px.box(df_temp, y="unit_price", x=feature, points="suspectedoutliers");
    fig.update_yaxes(range=[5000, 25000])


    print("----------------------------------------------------------------------------------------------------------------------------\n\n\n")

    


 Unit price distribution in split by district


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by market


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Building_material


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Building_ownership


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Building_type


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Construction_status


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Heating


----------------------------------------------------------------------------------------------------------------------------




 Unit price distribution in split by Windows_type


----------------------------------------------------------------------------------------------------------------------------





# Transforming data for ML models

In [16]:
from sklearn.preprocessing import OneHotEncoder

In [17]:
df_cat=df[unique_features]

In [18]:
enc=OneHotEncoder()
enc.fit(df_cat)

one_hot_val=enc.fit_transform(df_cat).toarray().astype(int)
one_hot_columns=enc.get_feature_names(unique_features)

OneHotEncoder(categories='auto', drop=None, dtype=<class 'numpy.float64'>,
              handle_unknown='error', sparse=True)

In [19]:
df_one_hot=pd.DataFrame(one_hot_val, columns=one_hot_columns)

In [20]:
df_one_hot.columns

Index(['district_Bemowo', 'district_Bialoleka', 'district_Bielany',
       'district_Downtown', 'district_Mokotow', 'district_Ochota',
       'district_Praga', 'district_Southern Praga', 'district_Subburbs',
       'district_Targowek', 'district_Ursynow', 'district_Wawer',
       'district_Wilanow', 'district_Wlochy', 'district_Wola',
       'district_Zoliborz', 'market_primary', 'market_secondary',
       'Building_material_breezeblock', 'Building_material_brick',
       'Building_material_cellular_concrete', 'Building_material_concrete',
       'Building_material_concrete_plate', 'Building_material_hydroton',
       'Building_material_not_specified', 'Building_material_other',
       'Building_material_reinforced_concrete', 'Building_material_silikat',
       'Building_material_wood', 'Building_ownership_co_operative_ownership',
       'Building_ownership_co_operative_ownership_with_a_land_and_mortgage_registe',
       'Building_ownership_full_ownership', 'Building_ownership_not_spec

In [21]:
not_specified_idx=[]
for i in range(0,df_one_hot.columns.shape[0]):
    if "not_specified" in df_one_hot.columns[i]:
        not_specified_idx.append(i)
not_specified_idx=np.asarray(not_specified_idx)

Let's drop all "not_specified" columns and secondary market in Mokotow district (it will be used as baseline in models)

In [22]:
drop_collinear_cols=list(df_one_hot.columns[not_specified_idx])
drop_collinear_cols.append('district_Mokotow')
drop_collinear_cols.append('market_secondary')

In [23]:
def list_diff(list1, list2):
    out = []
    for ele in list1:
        if not ele in list2:
            out.append(ele)
    return out

In [24]:
df_one_hot.columns

Index(['district_Bemowo', 'district_Bialoleka', 'district_Bielany',
       'district_Downtown', 'district_Mokotow', 'district_Ochota',
       'district_Praga', 'district_Southern Praga', 'district_Subburbs',
       'district_Targowek', 'district_Ursynow', 'district_Wawer',
       'district_Wilanow', 'district_Wlochy', 'district_Wola',
       'district_Zoliborz', 'market_primary', 'market_secondary',
       'Building_material_breezeblock', 'Building_material_brick',
       'Building_material_cellular_concrete', 'Building_material_concrete',
       'Building_material_concrete_plate', 'Building_material_hydroton',
       'Building_material_not_specified', 'Building_material_other',
       'Building_material_reinforced_concrete', 'Building_material_silikat',
       'Building_material_wood', 'Building_ownership_co_operative_ownership',
       'Building_ownership_co_operative_ownership_with_a_land_and_mortgage_registe',
       'Building_ownership_full_ownership', 'Building_ownership_not_spec

In [25]:
df_cat_columns=list_diff(df_one_hot.columns,drop_collinear_cols)

In [26]:
df_cat=df_one_hot[df_cat_columns]

In [27]:
columns_base=list_diff(df.columns, unique_features)

In [28]:
drop_columns_base=[
    'Price','latitude','longitude','lon_mod','lat_mod','grid_price','sample_size','City','subdistrict'
                  ]

In [29]:
columns_base=list_diff(columns_base, drop_columns_base)

In [30]:
df_base=df[columns_base]

In [31]:
df_base.columns

Index(['Id', 'Area', 'build_year', 'building_floors_num', 'rooms_num',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm',
       'Security_types_anti_burglary_door', 'Security_types_closed_area',
       'Security_types_entryphone', 'Security_types_monitoring',
       'Security_types_roller_shutters', 'floor_num', 'unit_price',


## Combining data for modeling

In [32]:
ml_data=pd.concat([df_base,df_cat],axis=1)

In [33]:
ml_data.shape

(11788, 89)

In [34]:
ml_data.head()

Id   Area  build_year  building_floors_num rooms_num  \
0  60534950  80.10        2021                    8         4   
1  60534789  52.27        2021                    8         2   
2  60534636  64.63        2021                    8         3   
3  60441425  46.86        2020                   14         3   
4  60225257  57.40        2019                   11         3   

   Equipment_types_dishwasher  Equipment_types_fridge  \
0                           0                       0   
1                           0                       0   
2                           0                       0   
3                           0                       0   
4                           1                       1   

   Equipment_types_furniture  Equipment_types_oven  Equipment_types_stove  \
0                          0                     0                      0   
1                          0                     0                      0   
2                          0                     0                      0   
3                          0                     0                      0   
4                          1                     1                      1   

   ...  Construction_status_to_completion  Construction_status_to_renovation  \
0  ...                                  0                                  0   
1  ...                                  0                                  0   
2  ...                                  0                                  0   
3  ...                                  0                                  0   
4  ...                                  0                                  0   

   Heating_boiler_room  Heating_electrical  Heating_gas  Heating_other  \
0                    0                   0            0              0   
1                    0                   0            0              0   
2                    0                   0            0              0   
3                    0                   0            0              0   
4                    0                   0            0              0   

   Heating_urban  Windows_type_aluminium  Windows_type_plastic  \
0              0                       0                     0   
1              0                       0                     0   
2              0                       0                     0   
3              0                       0                     0   
4              1                       0                     1   

   Windows_type_wooden  
0                    0  
1                    0  
2                    0  
3                    0  
4                    0  

[5 rows x 89 columns]

In [35]:
ml_data.columns[:]

Index(['Id', 'Area', 'build_year', 'building_floors_num', 'rooms_num',
       'Equipment_types_dishwasher', 'Equipment_types_fridge',
       'Equipment_types_furniture', 'Equipment_types_oven',
       'Equipment_types_stove', 'Equipment_types_tv',
       'Equipment_types_washing_machine', 'Extras_types_air_conditioning',
       'Extras_types_attic', 'Extras_types_balcony', 'Extras_types_basement',
       'Extras_types_garage', 'Extras_types_garden', 'Extras_types_lift',
       'Extras_types_separate_kitchen', 'Extras_types_terrace',
       'Extras_types_two_storey', 'Extras_types_usable_room',
       'Media_types_cable-television', 'Media_types_electricity',
       'Media_types_internet', 'Media_types_phone', 'Media_types_sewage',
       'Media_types_water', 'Security_types_alarm',
       'Security_types_anti_burglary_door', 'Security_types_closed_area',
       'Security_types_entryphone', 'Security_types_monitoring',
       'Security_types_roller_shutters', 'floor_num', 'unit_price',


# Selecting best features

In [36]:
counts, bins = np.histogram(ml_data.unit_price, bins=range(0, 50000, 1000))
bins = bins[1:]

fig = px.bar(x=bins, y=counts, labels={'x':'Unit price', 'y':'count'})
fig.show()

In [109]:
X=ml_data.copy()
X=X.query("unit_price<=25000 and unit_price>5000")
y=X.unit_price
X.drop(columns=["unit_price","Id"],inplace=True)

In [110]:
from sklearn.feature_selection import SelectKBest, f_regression, chi2

In [111]:
bestfeatures = SelectKBest(score_func=f_regression, k="all")

In [112]:
fit = bestfeatures.fit(X,y)
dfscores = pd.DataFrame(fit.scores_)
dfcolumns = pd.DataFrame(X.columns)

In [113]:
featureScores = pd.concat([dfcolumns,dfscores],axis=1)
featureScores.columns = ['Specs','Score']

In [114]:
featureScores.nlargest(30,'Score')

Specs        Score
35                   distance_driving  6889.140723
36                   distance_transit  6725.884253
38                       time_transit  5360.201112
37                       time_driving  4741.988679
42                  district_Downtown  3516.937318
40                 district_Bialoleka  1766.097573
75             Building_type_tenement   769.001425
54                     market_primary   701.343385
70                Building_type_block   629.435651
46                  district_Subburbs   582.320969
1                          build_year   515.887396
86                Windows_type_wooden   485.833201
69            Building_type_apartment   432.437679
76   Construction_status_ready_to_use   391.845786
77  Construction_status_to_completion   325.990756
2                 building_floors_num   323.696341
34                          floor_num   315.967698
3                           rooms_num   289.864371
11      Extras_types_air_conditioning   282.383245
52                      district_Wola   265.199542
13               Extras_types_balcony   188.918810
83                      Heating_urban   188.315507
6           Equipment_types_furniture   164.443512
16                Extras_types_garden   162.097546
56            Building_material_brick   158.490793
49                     district_Wawer   153.862225
39                    district_Bemowo   138.977967
67  Building_ownership_full_ownership   128.395893
4          Equipment_types_dishwasher   123.863883
25                  Media_types_phone   121.156862

In [115]:
featureScores.query("Score>40").shape

(51, 2)

In [116]:
top_features=featureScores.nlargest(50,'Score').Specs.unique()

In [117]:
featureScores.sort_values(by="Score",inplace=True,ascending=False)

import plotly.express as px
fig = px.bar(featureScores, x='Specs', y='Score')
fig.show()

In [118]:
X=X[top_features]

## Spliting into train and test sets

In [119]:
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)


In [120]:
y_train.reset_index(drop=True,inplace=True)
y_test.reset_index(drop=True,inplace=True)

X_train.reset_index(drop=True,inplace=True)
X_test.reset_index(drop=True,inplace=True)

# Training initial model

In [121]:
from sklearn.ensemble import RandomForestRegressor

## Hyper parameters selection

In [122]:
param_grid = [
   
    
    {"bootstrap":[True,False], "n_estimators":[200,400,600],
     "max_features":[6,9,18],"max_depth":[10,20,30],"min_samples_leaf":[3,10,30],"min_samples_split":[3,10,30]},
    
]

In [123]:
from sklearn.model_selection import GridSearchCV

In [124]:
forest_cl=RandomForestRegressor(random_state=10, n_jobs=4)

In [125]:
grid_search = GridSearchCV(forest_cl, param_grid, cv=5,
                          scoring="neg_mean_absolute_error",return_train_score=True)

In [126]:
grid_search.fit(X_train, y_train)
rf_clf_best_params = grid_search.best_estimator_
grid_search.best_params_

GridSearchCV(cv=5, error_score=nan,
             estimator=RandomForestRegressor(bootstrap=True, ccp_alpha=0.0,
                                             criterion='mse', max_depth=None,
                                             max_features='auto',
                                             max_leaf_nodes=None,
                                             max_samples=None,
                                             min_impurity_decrease=0.0,
                                             min_impurity_split=None,
                                             min_samples_leaf=1,
                                             min_samples_split=2,
                                             min_weight_fraction_leaf=0.0,
                                             n_estimators=100, n_jobs=4,
                                             oob_score=False, random_state=10,
                                             verbose=0, warm_start=False),
             iid='deprecated', n_jobs=No

{'bootstrap': False,
 'max_depth': 20,
 'max_features': 18,
 'min_samples_leaf': 3,
 'min_samples_split': 3,
 'n_estimators': 400}

In [127]:
grid_search.best_params_.keys()

dict_keys(['bootstrap', 'max_depth', 'max_features', 'min_samples_leaf', 'min_samples_split', 'n_estimators'])

In [128]:
rf_model=grid_search.best_estimator_

In [129]:
rf_model.fit(X_train,y_train)

RandomForestRegressor(bootstrap=False, ccp_alpha=0.0, criterion='mse',
                      max_depth=20, max_features=18, max_leaf_nodes=None,
                      max_samples=None, min_impurity_decrease=0.0,
                      min_impurity_split=None, min_samples_leaf=3,
                      min_samples_split=3, min_weight_fraction_leaf=0.0,
                      n_estimators=400, n_jobs=4, oob_score=False,
                      random_state=10, verbose=0, warm_start=False)

In [130]:
rf_model.score(X_train,y_train)

0.9401970427448834

In [131]:
rf_model.score(X_test,y_test)

0.708634770686344

In [132]:
importance_df=pd.DataFrame(rf_model.feature_importances_,columns=["coefficients"])
importance_df["features"]=X.columns
importance_df.sort_values(by="coefficients",inplace=True)

In [133]:

trace0=go.Bar(
        x=importance_df.coefficients,
        y=importance_df.features,
        orientation="h",
        
        marker=dict(
        color="blue",

        opacity=0.5
        ),
       
    )








data=[trace0]
figure=go.Figure(
    data=data,
    layout=go.Layout(
        title="RF Classifier - Feature importance",
        xaxis=dict(title="Importance"),
        yaxis=dict(title="Feature")

    
    ))
iplot(figure)

In [134]:
def performance_summary(model, X_train,y_train, X_test, y_test ):
    model.fit(X_train,y_train)
    y_hat=model.predict(X_test)
    
    df_summary=pd.DataFrame(y_hat, columns=["y_hat"])
    df_summary["y_true"]=y_test
    df_summary["predicted_rank"]=df_summary.y_hat.rank()
    df_summary["abs_error"]=np.abs(df_summary.y_true-df_summary.y_hat)
    df_summary["error"]=df_summary.y_hat-df_summary.y_true
    df_summary["relative_error"]= df_summary["error"]/df_summary.y_true
    df_summary["relative_abs_error"]= df_summary["abs_error"]/df_summary.y_true
    df_summary.sort_values(by="predicted_rank",inplace=True)
    df_summary.reset_index(drop=True, inplace=True)
    
    
    return(df_summary)
    

## Error analysis

In [135]:
df_summary=performance_summary(rf_model, X_train,y_train, X_test, y_test)

In [136]:
df_summary.describe()

y_hat        y_true  predicted_rank     abs_error         error  \
count   2330.000000   2330.000000     2330.000000   2330.000000   2330.000000   
mean   11119.769741  11115.604721     1165.500000   1021.119481      4.165020   
std     2454.688214   2986.134603      672.757328   1246.984771   1611.858044   
min     5987.363981   5357.000000        1.000000      0.202349 -11169.592568   
25%     9382.304561   9007.750000      583.250000    228.852416   -520.310956   
50%    10891.443205  10698.000000     1165.500000    611.052495     73.316285   
75%    12417.643510  12498.250000     1747.750000   1316.795374    684.922880   
max    23724.288801  25000.000000     2330.000000  11169.592568   8745.533128   

       relative_error  relative_abs_error  
count     2330.000000         2330.000000  
mean         0.018485            0.089540  
std          0.136819            0.105074  
min         -0.458933            0.000024  
25%         -0.046042            0.023177  
50%          0.007190            0.057121  
75%          0.068995            0.119578  
max          1.269677            1.269677

In [137]:
df_summary.head()

y_hat  y_true  predicted_rank    abs_error        error  \
0  5987.363981    6055             1.0    67.636019   -67.636019   
1  6293.419109    6745             2.0   451.580891  -451.580891   
2  6314.878006    7726             3.0  1411.121994 -1411.121994   
3  6322.406374    5829             4.0   493.406374   493.406374   
4  6443.194923    6416             5.0    27.194923    27.194923   

   relative_error  relative_abs_error  
0       -0.011170            0.011170  
1       -0.066950            0.066950  
2       -0.182646            0.182646  
3        0.084647            0.084647  
4        0.004239            0.004239

In [138]:


trace0=go.Scatter(
        name="Predicted",
        y=df_summary.y_hat,
        x=df_summary.predicted_rank,
        mode='lines',
        marker=dict(
        size=5,
        opacity=0.3
        ),
       
    )




trace1=go.Scatter(
        name="Actual",
        y=df_summary.y_true,
        x=df_summary.predicted_rank,
        mode='markers',
        marker=dict(
        color="blue",
    
        size=5,
        opacity=0.2
        ),
        text=df_summary.error
       
    )




data=[trace0,trace1]
figure=go.Figure(
    data=data,
    layout=go.Layout(
        title="Predicted vs actual unit price",
        yaxis=dict(title="Unit price",range=(0,25000)),
        xaxis=dict(title="Predicted rank")

    
    ))
iplot(figure)

In [139]:
counts, bins = np.histogram(df_summary.relative_error*100,bins=range(-50,50,2))
counts=counts/df_summary.shape[0]*100
bins=bins[1:]

In [140]:

fig = px.bar(x=bins, y=counts, labels={"x":"relative variance [%]", "y":"count"})
fig.show()

In [141]:
df_summary

y_hat  y_true  predicted_rank    abs_error        error  \
0      5987.363981    6055             1.0    67.636019   -67.636019   
1      6293.419109    6745             2.0   451.580891  -451.580891   
2      6314.878006    7726             3.0  1411.121994 -1411.121994   
3      6322.406374    5829             4.0   493.406374   493.406374   
4      6443.194923    6416             5.0    27.194923    27.194923   
...            ...     ...             ...          ...          ...   
2325  20866.073232   20204          2326.0   662.073232   662.073232   
2326  21435.168107   19928          2327.0  1507.168107  1507.168107   
2327  21946.261848   23043          2328.0  1096.738152 -1096.738152   
2328  23331.548307   24500          2329.0  1168.451693 -1168.451693   
2329  23724.288801   24000          2330.0   275.711199  -275.711199   

      relative_error  relative_abs_error  
0          -0.011170            0.011170  
1          -0.066950            0.066950  
2          -0.182646            0.182646  
3           0.084647            0.084647  
4           0.004239            0.004239  
...              ...                 ...  
2325        0.032769            0.032769  
2326        0.075631            0.075631  
2327       -0.047595            0.047595  
2328       -0.047692            0.047692  
2329       -0.011488            0.011488  

[2330 rows x 7 columns]

In [142]:
print("Share of forecasts within 25% absolute error {}".format(df_summary.query("relative_abs_error<0.25").shape[0]/df_summary.shape[0]))

Share of forecasts within 25% absolute error 0.9351931330472103


In [145]:
print("Share of forecasts within 10% absolute error {}".format(df_summary.query("relative_abs_error<0.10").shape[0]/df_summary.shape[0]))

Share of forecasts within 10% absolute error 0.6871244635193133


In [146]:
print("Share of forecasts within 5% absolute error {}".format(df_summary.query("relative_abs_error<0.05").shape[0]/df_summary.shape[0]))

SyntaxError: invalid syntax (<ipython-input-146-46bb5a9abf5a>, line 1)